In [1]:
import sys
from datetime import datetime

import gymnasium as gym
import numpy as np
import wandb
from stable_baselines3 import *
from stable_baselines3.common.callbacks import CallbackList
from stable_baselines3.common.logger import HumanOutputFormat
from stable_baselines3.common.logger import Logger as SB3Logger
from stable_baselines3.common.monitor import Monitor

import sinergym
import sinergym.utils.gcloud as gcloud
from sinergym.utils.callbacks import *
from sinergym.utils.constants import *
from sinergym.utils.logger import CSVLogger, WandBOutputFormat
from sinergym.utils.rewards import *
from sinergym.utils.wrappers import *

In [2]:
# Environment ID
environment = "Eplus-5zone-hot-continuous-stochastic-v1"
# Training episodes
episodes = 10
#Name of the experiment
experiment_date = datetime.today().strftime('%Y-%m-%d_%H:%M')
experiment_name = 'SB3_PPO-' + environment + \
    '-episodes-' + str(episodes)
experiment_name += '_' + experiment_date

In [3]:
# Create wandb.config object in order to log all experiment params
experiment_params = {
    'sinergym-version': sinergym.__version__,
    'python-version': sys.version
}
experiment_params.update({'environment':environment,
                          'episodes':episodes,
                          'algorithm':'SB3_DQN'})

# Get wandb init params (you have to specify your own project and entity)
wandb_params = {"project": 'sinergym',
                "entity": 'Huron-Yin'}
# Init wandb entry
run = wandb.init(
    name=experiment_name + '_' + wandb.util.generate_id(),
    config=experiment_params,
    ** wandb_params
)

Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: huron-yin. Use `wandb login --relogin` to force relogin


In [4]:
env = gym.make(environment, env_name=experiment_name)
eval_env = gym.make(environment, env_name=experiment_name+'_EVALUATION')

#==============================================================================================#
[ENVIRONMENT] (INFO) : Creating Gymnasium environment... [SB3_PPO-Eplus-5zone-hot-continuous-stochastic-v1-episodes-10_2024-04-14_21:15]
#==============================================================================================#
[MODELING] (INFO) : Experiment working directory created [/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-5zone-hot-continuous-stochastic-v1-episodes-10_2024-04-14_21:15-res35041]
[MODELING] (INFO) : Model Config is correct.
[MODELING] (INFO) : Updated building model with whole Output:Variable available names
[MODELING] (INFO) : Updated building model with whole Output:Meter available names
[MODELING] (INFO) : runperiod established: {'start_day': 1, 'start_month': 1, 'start_year': 1991, 'end_day': 31, 'end_month': 12, 'end_year': 1991, 'start_weekday': 0, 'n_steps_per_hour': 4}
[MODELING] (INFO) : Episode length (seconds): 31536000.0
[MODELING] (INFO) : timestep s

In [5]:
env = LoggerWrapper(env)
eval_env = LoggerWrapper(eval_env)

[WRAPPER LoggerWrapper] (INFO) : Wrapper initialized.
[WRAPPER LoggerWrapper] (INFO) : Wrapper initialized.


In [6]:
#model = DQN('MlpPolicy', env, verbose=1)
# model = PPO('MlpPolicy', env, learning_rate=0.0003, n_steps=2048, batch_size=64, n_epochs=10, gamma=0.99,
#             gae_lambda=0.95, clip_range=0.2, ent_coef=0, vf_coef=0.5, max_grad_norm=0.5, verbose=1, seed=3,
#             tensorboard_log=None)

model = PPO('MlpPolicy', env, learning_rate=0.001, n_steps=4096, batch_size=128, n_epochs=15, gamma=0.9,
            gae_lambda=0.9, clip_range=0.2, ent_coef=0, vf_coef=0.5, max_grad_norm=0.5, verbose=1, seed=3,
            tensorboard_log=None)

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


In [7]:
callbacks = []

# Set up Evaluation and saving best model
eval_callback = LoggerEvalCallback(
    eval_env,
    best_model_save_path=eval_env.get_wrapper_attr('workspace_path') +
    '/best_model/',
    log_path=eval_env.get_wrapper_attr('workspace_path') +
    '/best_model/',
    eval_freq=(eval_env.get_wrapper_attr('timestep_per_episode') - 1) * 2 - 1,
    deterministic=True,
    render=False,
    n_eval_episodes=1)
callbacks.append(eval_callback)


In [8]:
# wandb logger and setting in SB3
logger = SB3Logger(
    folder=None,
    output_formats=[
        HumanOutputFormat(
            sys.stdout,
            max_length=120),
        WandBOutputFormat()])
model.set_logger(logger)
# Append callback
log_callback = LoggerCallback()
callbacks.append(log_callback)


callback = CallbackList(callbacks)

In [9]:
timesteps = episodes * (env.get_wrapper_attr('timestep_per_episode') - 1)

In [10]:
model.learn(
    total_timesteps=timesteps,
    callback=callback,
    log_interval=1)

#----------------------------------------------------------------------------------------------#
[ENVIRONMENT] (INFO) : Starting a new episode... [SB3_PPO-Eplus-5zone-hot-continuous-stochastic-v1-episodes-10_2024-04-14_21:15] [Episode 1]
#----------------------------------------------------------------------------------------------#
[MODELING] (INFO) : Episode directory created [/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-5zone-hot-continuous-stochastic-v1-episodes-10_2024-04-14_21:15-res35041/Eplus-env-sub_run1]
[MODELING] (INFO) : Weather file USA_AZ_Davis-Monthan.AFB.722745_TMY3.epw used.
[MODELING] (INFO) : Adapting weather to building model. [USA_AZ_Davis-Monthan.AFB.722745_TMY3.epw]
[ENVIRONMENT] (INFO) : Saving episode output path... [/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-5zone-hot-continuous-stochastic-v1-episodes-10_2024-04-14_21:15-res35041/Eplus-env-sub_run1/output]


/usr/local/lib/python3.10/dist-packages/opyplus/weather_data/weather_data.py:493: FutureWarning: the 'line_terminator'' keyword is deprecated, use 'lineterminator' instead.
  epw_content = self._headers_to_epw(use_datetimes=use_datetimes) + df.to_csv(


[SIMULATOR] (INFO) : Running EnergyPlus with args: ['-w', '/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-5zone-hot-continuous-stochastic-v1-episodes-10_2024-04-14_21:15-res35041/Eplus-env-sub_run1/USA_AZ_Davis-Monthan.AFB.722745_TMY3_Random_1.0_0.0_0.001.epw', '-d', '/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-5zone-hot-continuous-stochastic-v1-episodes-10_2024-04-14_21:15-res35041/Eplus-env-sub_run1/output', '/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-5zone-hot-continuous-stochastic-v1-episodes-10_2024-04-14_21:15-res35041/Eplus-env-sub_run1/5ZoneAutoDXVAV.epJSON']
[ENVIRONMENT] (INFO) : Episode 1 started.
[SIMULATOR] (INFO) : handlers initialized.
[SIMULATOR] (INFO) : handlers are ready.
[SIMULATOR] (INFO) : System is ready.
[WRAPPER LoggerWrapper] (INFO) : Creating monitor.csv for current episode (episode 1) if logger is active
--------------------------------------------------------------------------------------------------------------| 1%
| action_network/                 |     

/workspaces/sinergym/sinergym/utils/callbacks.py:309: UserWarning: Training and eval env are not of the same type<stable_baselines3.common.vec_env.dummy_vec_env.DummyVecEnv object at 0x7f88c5bded10> != <LoggerWrapper<OrderEnforcing<PassiveEnvChecker<EplusEnv<Eplus-5zone-hot-continuous-stochastic-v1>>>>>
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/gymnasium/core.py:311: UserWarning: WARN: env.observation_variables to get variables from other wrappers is deprecated and will be removed in v1.0, to get this variable you can do `env.unwrapped.observation_variables` for environment variables or `env.get_wrapper_attr('observation_variables')` that will search the reminding wrappers.
  logger.warn(
/usr/local/lib/python3.10/dist-packages/gymnasium/core.py:311: UserWarning: WARN: env.action_variables to get variables from other wrappers is deprecated and will be removed in v1.0, to get this variable you can do `env.unwrapped.action_variables` for environment variables or `env.get_w

--------------------------------------------------------------------------------------------------------------| 1%
| action_network/                 |           |
|    Cooling_Setpoint_RL          | 23.25     |
|    Heating_Setpoint_RL          | 12.0      |
| action_simulation/              |           |
|    Cooling_Setpoint_RL          | 23.25     |
|    Heating_Setpoint_RL          | 12.0      |
| observation/                    |           |
|    HVAC_electricity_demand_rate | 117.9477  |
|    air_humidity                 | 16.438839 |
|    air_temperature              | 19.402603 |
|    clg_setpoint                 | 23.25     |
|    co2_emission                 | 0.0       |
|    day_of_month                 | 3.0       |
|    diffuse_solar_radiation      | 0.0       |
|    direct_solar_radiation       | 0.0       |
|    hour                         | 1.0       |
|    htg_setpoint                 | 12.0      |
|    month                        | 1.0       |
|    outdoor_humidity

...

[SIMULATOR] (INFO) : handlers are ready.
[SIMULATOR] (INFO) : System is ready.
[WRAPPER LoggerWrapper] (INFO) : Creating monitor.csv for current episode (episode 5) if logger is active
Progress: |***************************************************************************************************| 99%
[WRAPPER LoggerWrapper] (INFO) : End of episode, recording summary (progress.csv) if logger is active
[ENVIRONMENT] (INFO) : Environment closed. [SB3_PPO-Eplus-5zone-hot-continuous-stochastic-v1-episodes-10_2024-04-14_21:15_EVALUATION]
#----------------------------------------------------------------------------------------------#
[ENVIRONMENT] (INFO) : Starting a new episode... [SB3_PPO-Eplus-5zone-hot-continuous-stochastic-v1-episodes-10_2024-04-14_21:15] [Episode 11]
#----------------------------------------------------------------------------------------------#
[MODELING] (INFO) : Episode directory created [/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-5zone-hot-continuous-stochastic-v1-

/usr/local/lib/python3.10/dist-packages/opyplus/weather_data/weather_data.py:493: FutureWarning: the 'line_terminator'' keyword is deprecated, use 'lineterminator' instead.
  epw_content = self._headers_to_epw(use_datetimes=use_datetimes) + df.to_csv(


[WRAPPER LoggerWrapper] (INFO) : Creating monitor.csv for current episode (episode 11) if logger is active
Eval num_timesteps=350385, episode_reward=-8185.51 +/- 0.00
Episode length: 35040.00 +/- 0.00
-------------------------------------------------------
| action_network/                        |            |
|    Cooling_Setpoint_RL                 | 23.25      |
|    Heating_Setpoint_RL                 | 12.0       |
| action_simulation/                     |            |
|    Cooling_Setpoint_RL                 | 23.25      |
|    Heating_Setpoint_RL                 | 12.0       |
| eval/                                  |            |
|    comfort_violation(%)                | 30.5       |
|    cumulative_absolute_comfort_penalty | -9.49e+03  |
|    cumulative_absolute_energy_penalty  | -6.88e+07  |
|    cumulative_power_demand             | 6.88e+07   |
|    cumulative_reward                   | -8.19e+03  |
|    cumulative_reward_comfort_term      | -4.75e+03  |
|    cumulative

/usr/local/lib/python3.10/dist-packages/gymnasium/core.py:311: UserWarning: WARN: env.observation_variables to get variables from other wrappers is deprecated and will be removed in v1.0, to get this variable you can do `env.unwrapped.observation_variables` for environment variables or `env.get_wrapper_attr('observation_variables')` that will search the reminding wrappers.
  logger.warn(
/usr/local/lib/python3.10/dist-packages/gymnasium/core.py:311: UserWarning: WARN: env.action_variables to get variables from other wrappers is deprecated and will be removed in v1.0, to get this variable you can do `env.unwrapped.action_variables` for environment variables or `env.get_wrapper_attr('action_variables')` that will search the reminding wrappers.
  logger.warn(
/usr/local/lib/python3.10/dist-packages/gymnasium/core.py:311: UserWarning: WARN: env.is_discrete to get variables from other wrappers is deprecated and will be removed in v1.0, to get this variable you can do `env.unwrapped.is_discr

-----------------------------------------------
| action_network/                 |           |
|    Cooling_Setpoint_RL          | 23.25     |
|    Heating_Setpoint_RL          | 12.0      |
| action_simulation/              |           |
|    Cooling_Setpoint_RL          | 23.25     |
|    Heating_Setpoint_RL          | 12.0      |
| observation/                    |           |
|    HVAC_electricity_demand_rate | 176.78508 |
|    air_humidity                 | 27.825684 |
|    air_temperature              | 18.57636  |
|    clg_setpoint                 | 23.25     |
|    co2_emission                 | 0.0       |
|    day_of_month                 | 1.0       |
|    diffuse_solar_radiation      | 0.0       |
|    direct_solar_radiation       | 0.0       |
|    hour                         | 3.0       |
|    htg_setpoint                 | 12.0      |
|    month                        | 1.0       |
|    outdoor_humidity             | 67.0      |
|    outdoor_temperature          | 2.53

In [11]:
model.save(str(env.get_wrapper_attr('timestep_per_episode'))+ '/' + experiment_name)

In [12]:
env.close()

[WRAPPER LoggerWrapper] (INFO) : End of episode, recording summary (progress.csv) if logger is active


PermissionError: [Errno 13] Permission denied: '/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-5zone-hot-continuous-stochastic-v1-episodes-10_2024-04-14_21:15-res35041/progress.csv'

In [ ]:
artifact = wandb.Artifact(
        name="experiment1",
        type="training")
artifact.add_dir(
        env.get_wrapper_attr('workspace_path'),
        name='training_output/')
artifact.add_dir(
    eval_env.get_wrapper_attr('workspace_path'),
    name='evaluation_output/')
run.log_artifact(artifact)

# wandb has finished
run.finish()

wandb: Adding directory to artifact (/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-5zone-hot-continuous-stochastic-v1-episodes-10_2024-04-14_21:01-res35041)... 

Done. 0.9s
wandb: Adding directory to artifact (/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-5zone-hot-continuous-stochastic-v1-episodes-10_2024-04-14_21:01_EVALUATION-res35041)... Done. 0.4s


In [ ]:
# Environment ID
environment = "Eplus-5zone-hot-discrete-stochastic-v1"
# Episodes
episodes=20
# Evaluation name
evaluation_date = datetime.today().strftime('%Y-%m-%d_%H:%M')
evaluation_name = 'SB3_DQN-EVAL-' + environment + \
    '-episodes-' + str(episodes)
evaluation_name += '_' + evaluation_date

In [ ]:

# Create wandb.config object in order to log all experiment params
experiment_params = {
    'sinergym-version': sinergym.__version__,
    'python-version': sys.version
}
experiment_params.update({'environment':environment,
                          'episodes':episodes,
                          'algorithm':'SB3_DQN'})

wandb_params = {"project": 'sinergym_evaluations',
                "entity": 'huron-yin'}
# Init wandb entry
run = wandb.init(
    name=experiment_name + '_' + wandb.util.generate_id(),
    config=experiment_params,
    ** wandb_params
)

In [ ]:
env = gym.make(environment, env_name=evaluation_name)
env = LoggerWrapper(env)

#==============================================================================================#
[ENVIRONMENT] (INFO) : Creating Gymnasium environment... [SB3_DQN-EVAL-Eplus-5zone-hot-discrete-stochastic-v1-episodes-20_2024-04-14_21:12]
#==============================================================================================#
[MODELING] (INFO) : Experiment working directory created [/workspaces/sinergym/Eplus-env-SB3_DQN-EVAL-Eplus-5zone-hot-discrete-stochastic-v1-episodes-20_2024-04-14_21:12-res35041]
[MODELING] (INFO) : Model Config is correct.
[MODELING] (INFO) : Updated building model with whole Output:Variable available names
[MODELING] (INFO) : Updated building model with whole Output:Meter available names
[MODELING] (INFO) : runperiod established: {'start_day': 1, 'start_month': 1, 'start_year': 1991, 'end_day': 31, 'end_month': 12, 'end_year': 1991, 'start_weekday': 0, 'n_steps_per_hour': 4}
[MODELING] (INFO) : Episode length (seconds): 31536000.0
[MODELING] (INFO) : time

In [ ]:
# get wandb artifact path (to load model)
load_artifact_entity = 'huron-yin'
load_artifact_project = 'sinergym'
load_artifact_name = 'experiment1'
load_artifact_tag = 'latest'
load_artifact_model_path = 'evaluation_output/best_model/model.zip'
wandb_path = load_artifact_entity + '/' + load_artifact_project + \
    '/' + load_artifact_name + ':' + load_artifact_tag
# Download artifact
artifact = run.use_artifact(wandb_path)
artifact.get_path(load_artifact_model_path).download('.')
# Set model path to local wandb file downloaded
model_path = './' + load_artifact_model_path
model = DQN.load(model_path)

wandb: WARNING Artifact.get_path(name) is deprecated, use Artifact.get_entry(name) instead.


AttributeError: 'ActorCriticPolicy' object has no attribute 'q_net'

In [ ]:
for i in range(episodes):
    obs, info = env.reset()
    rewards = []
    truncated = terminated = False
    current_month = 0
    while not (terminated or truncated):
        a, _ = model.predict(obs)
        obs, reward, terminated, truncated, info = env.step(a)
        rewards.append(reward)
        if info['month'] != current_month:
            current_month = info['month']
            print(info['month'], sum(rewards))
    print(
        'Episode ',
        i,
        'Mean reward: ',
        np.mean(rewards),
        'Cumulative reward: ',
        sum(rewards))
env.close()

#----------------------------------------------------------------------------------------------#
[ENVIRONMENT] (INFO) : Starting a new episode... [SB3_DQN-EVAL-Eplus-5zone-mixed-discrete-stochastic-v1-episodes-20_2024-04-14_01:19] [Episode 1]
#----------------------------------------------------------------------------------------------#
[MODELING] (INFO) : Episode directory created [/workspaces/sinergym/Eplus-env-SB3_DQN-EVAL-Eplus-5zone-mixed-discrete-stochastic-v1-episodes-20_2024-04-14_01:19-res35041/Eplus-env-sub_run1]
[MODELING] (INFO) : Weather file USA_NY_New.York-J.F.Kennedy.Intl.AP.744860_TMY3.epw used.
[MODELING] (INFO) : Adapting weather to building model. [USA_NY_New.York-J.F.Kennedy.Intl.AP.744860_TMY3.epw]
[ENVIRONMENT] (INFO) : Saving episode output path... [/workspaces/sinergym/Eplus-env-SB3_DQN-EVAL-Eplus-5zone-mixed-discrete-stochastic-v1-episodes-20_2024-04-14_01:19-res35041/Eplus-env-sub_run1/output]
[SIMULATOR] (INFO) : Running EnergyPlus with args: ['-w', '/works

/usr/local/lib/python3.10/dist-packages/opyplus/weather_data/weather_data.py:493: FutureWarning: the 'line_terminator'' keyword is deprecated, use 'lineterminator' instead.
  epw_content = self._headers_to_epw(use_datetimes=use_datetimes) + df.to_csv(


[SIMULATOR] (INFO) : handlers initialized.
[SIMULATOR] (INFO) : handlers are ready.
[SIMULATOR] (INFO) : System is ready.
[WRAPPER LoggerWrapper] (INFO) : Creating monitor.csv for current episode (episode 1) if logger is active
1 -1.8198065800890029


/usr/local/lib/python3.10/dist-packages/gymnasium/spaces/box.py:240: UserWarning: WARN: Casting input x to numpy array.
  gym.logger.warn("Casting input x to numpy array.")


2 -1456.482602025735------------------------------------------------------------------------------------------| 9%
3 -2807.473352502696*******-----------------------------------------------------------------------------------| 16%
4 -3630.8199392341744***************--------------------------------------------------------------------------| 25%
5 -4171.4544253910135***********************------------------------------------------------------------------| 33%
6 -4914.514877177401********************************----------------------------------------------------------| 41%
7 -6090.695391428426*****************************************-------------------------------------------------| 50%
8 -7125.827900716757************************************************------------------------------------------| 58%
9 -8118.046438289979*********************************************************---------------------------------| 66%
10 -9332.17535905157*****************************************************

...

2 -1468.5607110685457-----------------------------------------------------------------------------------------| 9%
3 -2848.854431373982*******-----------------------------------------------------------------------------------| 16%
4 -3713.0480751998402***************--------------------------------------------------------------------------| 25%
5 -4289.97637193289*************************------------------------------------------------------------------| 33%
6 -5045.590638944164********************************----------------------------------------------------------| 41%
7 -6209.2463174456425****************************************-------------------------------------------------| 50%
8 -7259.490882295762************************************************------------------------------------------| 58%
9 -8233.918151452852*********************************************************---------------------------------| 66%
10 -9469.113722652572****************************************************

/usr/local/lib/python3.10/dist-packages/opyplus/weather_data/weather_data.py:493: FutureWarning: the 'line_terminator'' keyword is deprecated, use 'lineterminator' instead.
  epw_content = self._headers_to_epw(use_datetimes=use_datetimes) + df.to_csv(


[SIMULATOR] (INFO) : handlers are ready.
[SIMULATOR] (INFO) : System is ready.
[WRAPPER LoggerWrapper] (INFO) : Creating monitor.csv for current episode (episode 20) if logger is active
1 -1.8755936850490802


/usr/local/lib/python3.10/dist-packages/gymnasium/spaces/box.py:240: UserWarning: WARN: Casting input x to numpy array.
  gym.logger.warn("Casting input x to numpy array.")


2 -1454.5674716300903-----------------------------------------------------------------------------------------| 9%
3 -2838.8357210230583******-----------------------------------------------------------------------------------| 16%
4 -3637.574117221302****************--------------------------------------------------------------------------| 25%
5 -4220.77290877749*************************------------------------------------------------------------------| 33%
6 -4977.291611356344********************************----------------------------------------------------------| 41%
7 -6160.0989555803735****************************************-------------------------------------------------| 50%
8 -7211.268806977147************************************************------------------------------------------| 58%
9 -8217.415907543766*********************************************************---------------------------------| 66%
10 -9456.846171189427****************************************************

In [ ]:
artifact = wandb.Artifact(
    name="evaluation1",
    type="evaluating")
artifact.add_dir(
    env.experiment_path,
    name='evaluation_output/')

run.log_artifact(artifact)

# wandb has finished
run.finish()

/usr/local/lib/python3.10/dist-packages/gymnasium/core.py:311: UserWarning: WARN: env.experiment_path to get variables from other wrappers is deprecated and will be removed in v1.0, to get this variable you can do `env.unwrapped.experiment_path` for environment variables or `env.get_wrapper_attr('experiment_path')` that will search the reminding wrappers.
  logger.warn(


AttributeError: 'EplusEnv' object has no attribute 'experiment_path'